## Описание проекта

Нам предстоит работать с псевдо-реальными (реальные данные в которые добавлена синтетическая составляющая) данными о стартапах, функционировавших в период с 1970 по 2018 годы, и предсказать, какие из них закроются.


Описание полей данных
- `name` - Название стартапа
- `category_list` - Список категорий, к которым относится стартап
- `funding_total_usd` - Общая сумма финансирования в USD
- `status` - Статус стартапа (закрыт или действующий), **целевой признак**
- `country_code` - Код страны
- `state_code` - Код штата
- `region` - Регион
- `city` - Город
- `funding_rounds` - Количество раундов финансирования
- `founded_at` - Дата основания
- `first_funding_at` - Дата первого раунда финансирования
- `last_funding_at` - Дата последнего раунда финансирования
- `closed_at` - Дата закрытия стартапа (если применимо)
- `lifetime` - Время существования стартапа в днях

In [24]:
# imports
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from ydata_profiling import ProfileReport

import phik
import shap

 ## Загрузка и проверка данных

In [25]:
# Импортируем тренировочный датасет
df = pd.read_csv('data/startup_train.csv',
                 parse_dates=['founded_at', 'first_funding_at', 'last_funding_at', 'closed_at'])

# Импортируем тестовый датасет
test_df = pd.read_csv('data/startup_test.csv',
                      parse_dates=['first_funding_at', 'last_funding_at', ])

In [26]:
# Выводим информацию о тренировочном датасете
print(df.info())
df

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 52516 entries, 0 to 52515
Data columns (total 13 columns):
 #   Column             Non-Null Count  Dtype         
---  ------             --------------  -----         
 0   name               52515 non-null  object        
 1   category_list      50051 non-null  object        
 2   funding_total_usd  42447 non-null  float64       
 3   status             52516 non-null  object        
 4   country_code       47014 non-null  object        
 5   state_code         45753 non-null  object        
 6   region             46157 non-null  object        
 7   city               46157 non-null  object        
 8   funding_rounds     52516 non-null  int64         
 9   founded_at         52516 non-null  datetime64[ns]
 10  first_funding_at   52516 non-null  datetime64[ns]
 11  last_funding_at    52516 non-null  datetime64[ns]
 12  closed_at          4917 non-null   datetime64[ns]
dtypes: datetime64[ns](4), float64(1), int64(1), object(7)
memory 

name                           category_list  \
0                   Lunchgate         Online Reservations|Restaurants   
1                     EarLens   Manufacturing|Medical|Medical Devices   
2      Reviva Pharmaceuticals                           Biotechnology   
3        Sancilio and Company                             Health Care   
4         WireTough Cylinders                           Manufacturing   
...                       ...                                     ...   
52511             Videostream                           Entertainment   
52512             Hello Curry                             Hospitality   
52513               Taskforce   Email|Messaging|Productivity Software   
52514               NetScaler                                Security   
52515              Apparcando  Online Rental|Parking|Price Comparison   

       funding_total_usd     status country_code state_code       region  \
0               828626.0  operating          CHE         25       Zurich   
1             42935019.0  operating          USA         CA  SF Bay Area   
2             35456381.0  operating          USA         CA  SF Bay Area   
3             22250000.0  operating          NaN        NaN          NaN   
4                    NaN  operating          USA         VA   VA - Other   
...                  ...        ...          ...        ...          ...   
52511                NaN  operating          CAN         ON      Toronto   
52512           500000.0  operating          IND          2    Hyderabad   
52513            50000.0  operating          USA         CA  SF Bay Area   
52514         13000000.0  operating          USA         CA  SF Bay Area   
52515           270820.0  operating          ESP         60     Valencia   

                city  funding_rounds founded_at first_funding_at  \
0             Zürich               2 2009-10-17       2011-05-01   
1       Redwood City               4 2005-01-01       2010-05-04   
2           San Jose               3 2006-01-01       2012-08-20   
3                NaN               3 2004-01-01       2011-09-01   
4            Bristol               1 2010-05-12       2012-02-01   
...              ...             ...        ...              ...   
52511      Kitchener               1 2012-01-01       2014-03-01   
52512      Hyderabad               1 2013-08-25       2014-03-07   
52513  San Francisco               3 2010-07-01       2009-06-14   
52514       San Jose               6 1997-12-01       1998-11-30   
52515       Valencia               1 2012-08-11       2014-06-13   

      last_funding_at closed_at  
0          2014-12-01       NaT  
1          2014-02-25       NaT  
2          2014-07-02       NaT  
3          2014-07-18       NaT  
4          2012-02-01       NaT  
...               ...       ...  
52511      2014-03-01       NaT  
52512      2014-03-07       NaT  
52513      2011-01-01       NaT  
52514      2004-03-01       NaT  
52515      2014-06-13       NaT  

[52516 rows x 13 columns]

Мы видим, что большинство данных у нас приведены к корректному типу данных. Мы можем привести столбец `status` к булевому типу, так как он принимает всего 2 значения: closed и operating. Сделаем это позже, используя label encoder. У нас в тренировочных данных присутствует столбец `closed_at`. Удалим его, так как это будет являться утечкой целевого признака

In [27]:
# Выводим информацию о тестовом датасете
print(test_df.info())
test_df

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 13125 entries, 0 to 13124
Data columns (total 11 columns):
 #   Column             Non-Null Count  Dtype         
---  ------             --------------  -----         
 0   name               13125 non-null  object        
 1   category_list      12534 non-null  object        
 2   funding_total_usd  10547 non-null  float64       
 3   country_code       11743 non-null  object        
 4   state_code         11430 non-null  object        
 5   region             11536 non-null  object        
 6   city               11538 non-null  object        
 7   funding_rounds     13125 non-null  int64         
 8   first_funding_at   13125 non-null  datetime64[ns]
 9   last_funding_at    13125 non-null  datetime64[ns]
 10  lifetime           13125 non-null  int64         
dtypes: datetime64[ns](2), float64(1), int64(2), object(6)
memory usage: 1.1+ MB
None


name  \
0                  Crystalsol   
1            JBI Fish & Wings   
2                    COINPLUS   
3      Imagine Communications   
4                       DNA13   
...                       ...   
13120                   Jymob   
13121               GlobaTrek   
13122                Inkd.com   
13123                  AdWill   
13124             RingCentral   

                                           category_list  funding_total_usd  \
0                                       Clean Technology          2819200.0   
1                                            Hospitality                NaN   
2                                                Finance           428257.0   
3                         Software|Video|Video Streaming         34700000.0   
4                                               Software          4530000.0   
...                                                  ...                ...   
13120                                         Recruiting            28000.0   
13121                                           Software                NaN   
13122            Design|E-Commerce|Marketplaces|Printing          5600000.0   
13123    Advertising Exchanges|Mobile|Mobile Advertising           150000.0   
13124  Communications Hardware|Messaging|Mobile|Offic...         50250000.0   

      country_code state_code            region              city  \
0              NIC         17               NaN               NaN   
1              USA         TN        TN - Other          Humboldt   
2              LUX          3  Esch-sur-alzette  Esch-sur-alzette   
3              USA         CA         San Diego         San Diego   
4              CAN         ON            Ottawa            Ottawa   
...            ...        ...               ...               ...   
13120          USA         CA       SF Bay Area         Sunnyvale   
13121          USA         CA       SF Bay Area     Mountain View   
13122          USA         WA           Seattle           Seattle   
13123          USA         NY     New York City          New York   
13124          USA         CA       SF Bay Area         San Mateo   

       funding_rounds first_funding_at last_funding_at  lifetime  
0                   1       2009-07-01      2009-07-01      3501  
1                   1       2010-07-28      2010-07-28      2717  
2                   2       2014-05-15      2014-09-18      1295  
3                   4       2005-01-01      2010-04-20      4748  
4                   1       2007-05-08      2007-05-08      6209  
...               ...              ...             ...       ...  
13120               1       2012-07-01      2012-07-01      2267  
13121               1       2013-10-01      2013-10-01      2192  
13122               3       2008-09-01      2011-06-28      2922  
13123               2       2014-09-27      2014-11-04      1386  
13124               6       2007-01-16      2012-11-21      5479  

[13125 rows x 11 columns]

В тестовом датасете данные все данные так же приведены к правильному типу данных. Столбец `lifetime` нам придется удалить, так как он не фигурирует в обучающих данных. Мы могли бы посчитать `lifetime` в тренировочной таблице, однако это будет утечкой целевого признака, так как для компаний, которые все еще не закрылись, данных не будет

### Вывод:

Мы видим, что большинство данных у нас приведены к корректному типу данных. Мы можем привести столбец `status` к булевому типу, так как он принимает всего 2 значения: closed и operating. Сделаем это позже, используя label encoder. У нас в тренировочных данных присутствует столбец `closed_at`. Удалим его, так как это будет являться утечкой целевого признака.

В тестовом датасете данные все данные так же приведены к правильному типу данных. Столбец `lifetime` нам придется удалить, так как он не фигурирует в обучающих данных. Мы могли бы посчитать `lifetime` в тренировочной таблице, однако это будет утечкой целевого признака, так как для компаний, которые все еще не закрылись, данных не будет


## Предобработка данных:

Посмотрим на наличие выбросов и пропусков. Обработаем их, если возможно

In [ ]:
# Объявим список числовых, категориальных, и столбцов с датой
num_col_names = ['funding_total_usd', 'funding_rounds' ]
cat_col_names = ['category_list', 'country_code', 'state_code', 'region', 'city']
date_col_names = ['founded_at', 'first_funding_at', 'last_funding_at', 'closed_at']

In [29]:
# Создаем отчет до обработки тренировочных данных, используя ydata-profiling
profile = ProfileReport(df, title='Report before train data processing')

# Сохраняем отчет
profile.to_file('reports/report_before_train_data_processing.html')

# Выводим отчет
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [30]:
# Создаем отчет до обработки тестовых данных, используя ydata-profiling
profile = ProfileReport(test_df, title='Report before test data processing')

# Сохраняем отчет
profile.to_file('reports/report_before_test_data_processing.html')

# Выводим отчет
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]